# An Interpreter in Python

## Language Syntax

```
<prog> ::=  <defs> <expr>

<defs> ::=  fun <id> (<id>*) { <expr> } <defs> |  ε 

<expr> ::=  <expr> + <expr> | <expr> - <expr> | <expr> * <expr> 
          | <n> | <id> | <id> (<expr>*)

          | inc()          // increase a global counter 
          | print(<expr>)  // evaluate an expression, print it, and return it

<id> ::= ... // an identifier

<n> ::= ... // and integer literal
```



Example program

```
fun foo(x,y,z) { ( x + y ) * z }
fun bar(w) { w + 1 }

foo(1,1,3) * bar(6)
```

Task: Write an interpreter that takes a program of this language, it evaluates it, and prints an an integer which is the result of the evaluation.

The interpreter takes two parameters: 
- `prog`, a dictionary that represents the abstract syntax tree of the input program (see below).
- `eval_mode`, which a string that specifies the parameter-passing strategy. It can be 'cbv' (call-by-name), 'cbn' (call-by-value), 'lazy' (call-by-need).

AST represtantion:

- `<prog>` is represented as  `{ 'defs' : <defs>, 'main' : <expr> }`
- `<defs>` is represented as a list of dictionaries of the form `{ 'name' : <string>, 'params' : <strings>, 'body' : <expr> }`

- `<expr>` has one of the following forms
    - `{ 'kind':'op', 'op':<op>,'lhs':<expr>,'rhs' : <expr> }` 
    - `{ 'kind':'var', 'var': <string> }` 
    - `{ 'kind':'num', 'num': <num> }`
    - `{ 'kind':'call', 'name': <string>, 'args':<exprs> }`
    - `{ 'kind':'inc' }`
    - `{ 'kind':'print', 'arg': <expr> }`
       
where `<op>` is one of the strings `'add'`, `'sub'` or `'mul'`, `<num>` is an integer, `<string>` a string, and `<exprs>` a list of `<expr>` dictionaries.


For example, the program 
```
def foo(x,y,z) { x + (y * z) }
def bar(w) { w + 42 } 
foo(42,1+2,2*11) * bar(5 - 3)
```
is represented as follows

In [7]:
# def foo(x, y, z) { x + (y * z) }
# def bar(w) { w + 42 }
funs = [
    {
        'name': 'foo',
        'params': ['x', 'y', 'z'],
        'body': {
            'kind': 'op',
            'op': 'add',
            'lhs': { 'kind': 'var', 'var': 'x' },
            'rhs': {
                'kind': 'op',
                'op': 'mul',
                'lhs': { 'kind': 'var', 'var': 'y' },
                'rhs': { 'kind': 'var', 'var': 'z' }
            }
        }
    },
    {
        'name': 'bar',
        'params': ['w'],
        'body': {
            'kind': 'op',
            'op': 'add',
            'lhs': { 'kind': 'var', 'var': 'w' },
            'rhs': { 'kind': 'num', 'num': 42 }
        }
    }
]

# 1 + 2
add_expr = {
    'kind': 'op',
    'op': 'add',
    'lhs': { 'kind': 'num', 'num': 1 },
    'rhs': { 'kind': 'num', 'num': 2 }
}

# 2 * 11
mul_expr = {
    'kind': 'op',
    'op': 'mul',
    'lhs': { 'kind': 'num', 'num': 2 },
    'rhs': { 'kind': 'num', 'num': 11 }
}

# 5 - 3
sub_expr = {
    'kind': 'op',
    'op': 'sub',
    'lhs': { 'kind': 'num', 'num': 5 },
    'rhs': { 'kind': 'num', 'num': 3 }
}

# foo(42, 1 + 2, 2 * 11) * bar(5 - 3)
body = {
    'kind': 'op',
    'op': 'mul',
    'lhs': {
        'kind': 'call',
        'name': 'foo',
        'args': [
            { 'kind': 'num', 'num': 42 },  # 42
            add_expr,                      # 1 + 2
            mul_expr                       # 2 * 11
        ]
    },
    'rhs': {
        'kind': 'call',
        'name': 'bar',
        'args': [sub_expr]                 # 5 - 3
    }
}

# Full program:
# def foo(x, y, z) { x + (y * z) }
# def bar(w) { w + 42 }
# foo(42, 1 + 2, 2 * 11) * bar(5 - 3)
prog = {
    'defs': funs,
    'body': body
}

# 1 + 2
prog1 = {
    'defs': [],
    'body': add_expr
}

## Solution

In [8]:
defs = {} # a dictionary for the global functions
mode = "cbv" # parameter passing mode
counter = 0

# the main evaluation function
def eval(expr, env):
    match expr['kind']:
        case 'num': return expr['num']
        case 'op':
            op = expr['op']
            lhs = eval(expr['lhs'], env)
            rhs = eval(expr['rhs'], env)
            match op:
                case 'add': return (lhs + rhs)
                case 'mul': 
                    return (lhs * rhs)
                case 'sub': return (lhs - rhs)
                case 'div': return (lhs / rhs)
        case 'var':
            var = expr['var']
            match mode:
                case 'cbv': return env[var]
                case 'cbn': return env[var]()
                case 'lazy':
                    val = env[var]()
                    env[var] = lambda res = val: res
                    return val
                    
        case 'call': 
            f = expr['name']
            args = expr['args']
            (vars, body) = defs[f]
            
            match mode:
                case 'cbv':
                    env_new = {}
                    for (var, arg) in zip(vars, args):
                        env_new[var] = eval(arg,env)
                    return eval(body, env_new)                      
                case 'cbn':
                    env_new = {}
                    for (var, arg) in zip(vars, args):
                        env_new[var] = lambda expr = arg: eval(expr,env)
                    return eval(body, env_new)                      

                case 'lazy':
                    env_new = {}
                    for (var, arg) in zip(vars, args):
                        env_new[var] = lambda expr = arg: eval(expr,env)
                    return eval(body, env_new)                      
      
        case 'inc': 
            global counter
            counter += 1
            return counter

        case 'print': 
            res = eval(expr['arg'], env)
            print(res)
            return res

def add_defs(funs):
  for fun in funs:
      defs[fun['name']] = (fun['params'], fun['body'])
    
def eval_prog(prog, eval_mode): 
    global mode
    global counter
    counter = 0
    mode = eval_mode
    add_defs(prog['defs'])
    return eval(prog['body'], {})


In [9]:
# testing
print(eval_prog(prog, "cbv"))
print(eval_prog(prog, "cbn"))
print(eval_prog(prog, "lazy"))

4752
4752
4752


**Challenge**: Come up with programs that evaluate differently with each parameter passing style.

In [10]:
# def f(x) { x + x } 
# f(inc())


prog2 = {
    'defs': [
        {
            'name': 'f',
            'params': ['x'],
            'body': {
                'kind': 'op',
                'op': 'add',
                'lhs': {'kind': 'var', 'var': 'x'},
                'rhs': {'kind': 'var', 'var': 'x'}
            }
        }
    ],
    'body': {
        'kind': 'call',
        'name': 'f',
        'args': [ {'kind': 'inc'} ]
    }
}
print(eval_prog(prog2, "cbv"))
print(eval_prog(prog2, "cbn"))
print(eval_prog(prog2, "lazy"))

2
3
2


In [11]:
# def f(x, y) { x + inc()}
# f(10, inc())

funs = [
    {
        'name': 'f',
        'params': ['x', 'y'],
        'body': {
            'kind': 'op',
            'op': 'add',
            'lhs': { 'kind': 'var', 'var': 'x' },
            'rhs': { 'kind': 'inc' }  # inc() is treated as a special form
        }
    }
]

body = {
    'kind': 'call',
    'name': 'f',
    'args': [
        { 'kind': 'num', 'num': 10 },  # 10
        { 'kind': 'inc' }              # inc()
    ]
}

prog3 = {
    'defs': funs,
    'body': body
}

print(eval_prog(prog3, "cbv"))
print(eval_prog(prog3, "cbn"))
print(eval_prog(prog3, "lazy"))

12
11
11


In [12]:
# def f(x, y) { x + x}
# f(print(21),print(11))

funs = [
    {
        'name': 'f',
        'params': ['x', 'y'],
        'body': {
            'kind': 'op',
            'op': 'add',
            'lhs': { 'kind': 'var', 'var': 'x' },
            'rhs': { 'kind': 'var', 'var': 'x' }
        }
    }
]

body = {
    'kind': 'call',
    'name': 'f',
    'args': [
        { 'kind': 'print', 'arg': { 'kind': 'num', 'num': 21 } },  # print(21)
        { 'kind': 'print', 'arg': { 'kind': 'num', 'num': 11 } }   # print(11)
    ]
}

prog4 = {
    'defs': funs,
    'body': body
}

print("CBV:")
print(eval_prog(prog4, "cbv"))
print("CBN:")
print(eval_prog(prog4, "cbn"))
print("Lazy:")
print(eval_prog(prog4, "lazy"))

CBV:
21
11
42
CBN:
21
21
42
Lazy:
21
42
